In [42]:
import os
import sys
import re
import argparse
import shutil
import numpy as np
import pandas as pd
from tqdm import tqdm

In [43]:
#organism_name = "Chlamydia psittaci"
organism_name = "Vibrio campbellii"
lst = organism_name.split()
lst = re.split(" |_", organism_name)
if len(lst[-1]) < 10:
    last_letter = len(lst[-1])
else:
    last_letter = 9
folder_name = f"{lst[0][0]}_{lst[-1][:last_letter]}"

### Orto rows with singletons, but without paralog-containing rows

In [3]:
# Uploading and modificating orto rows tables
orto_rows = pd.read_csv(f"../{folder_name}/data/{folder_name}.proteinortho.tsv", sep="\t") # Uploading dataframe with orto rows
orto_rows = orto_rows.rename(columns = {"# Species": "Species"})
orto_rows["ortologus_row"] = orto_rows.index + 1 # Creating ortorows numbers

# Uploading first csv-table and creating a new column in it
orto_rows_list = orto_rows.index
df1 = pd.read_csv(f"../{folder_name}/data/First_table.csv")

In [4]:
#Filling orto_row column (sounds like an oxymoron)
assemblies = orto_rows.columns[3:-1]
row_assigner = pd.melt(orto_rows, id_vars=["ortologus_row"], value_vars=assemblies)
row_assigner = row_assigner.query("value != '*'")
row_assigner["value"] = row_assigner["value"].str[:14]
row_assigner
row_assigner.drop(["variable"], axis="columns", inplace=True)
row_assigner.columns = ["ortologus_row", "id"]
df1 = df1.merge(row_assigner, on="id")

In [5]:
# Number of the paralogs
print("Number of the paralogs =", sum(orto_rows.query("Genes > Species").Genes) - sum(orto_rows.query("Genes > Species").Species))

Number of the paralogs = 2719


In [6]:
# Creating a subset without pararows
pararows_numbers = orto_rows.query("Genes > Species").ortologus_row
df1 = df1.query("ortologus_row not in @pararows_numbers").query("ortologus_row != 0")

In [7]:
# Compiling data about start-codons of ortologus rows
start_codon_per_row = df1.groupby("ortologus_row", as_index=False).agg({"start_codone": ".".join})
start_codon_per_row["start_codone"]
orr_start_list = []
for number in tqdm(range(len(start_codon_per_row))):
    orr_start_list.append(start_codon_per_row.iloc[number, 1].split("."))
start_codons = pd.DataFrame(
    {
        "ortologus_row": start_codon_per_row["ortologus_row"],
        "start_codons": pd.Series(orr_start_list),
        "ATG": 0.0,
        "GTG": 0.0,
        "TTG": 0.0,
    }
)

# Computing frequencies of exact start-codons
start_codons.sort_values("ortologus_row", inplace=True)
for row in tqdm(range(len(start_codons))):
    freqs = pd.Series(start_codons["start_codons"][row]).value_counts() # If it will be need to visualize percents, use normalize=True in brackets
    rowlength = len(start_codons["start_codons"][row])
    if "ATG" in freqs:
        start_codons["ATG"][row] = freqs["ATG"]
    else:
        start_codons["ATG"][row] = 0
    if "GTG" in freqs:
        start_codons["GTG"][row] = freqs["GTG"]
    else:
        start_codons["GTG"][row] = 0
    if "TTG" in freqs:
        start_codons["TTG"][row] = freqs["TTG"]
    else:
        start_codons["TTG"][row] = 0

  0%|                                                                                                              | 0/12356 [00:00<?, ?it/s]/tmp/ipykernel_18850/1259367515.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["ATG"][row] = freqs["ATG"]
/tmp/ipykernel_18850/1259367515.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["GTG"][row] = 0
/tmp/ipykernel_18850/1259367515.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returni

  1%|█                                                                                                 | 140/12356 [00:00<00:08, 1391.74it/s]/tmp/ipykernel_18850/1259367515.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["ATG"][row] = freqs["ATG"]
/tmp/ipykernel_18850/1259367515.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["GTG"][row] = freqs["GTG"]
/tmp/ipykernel_18850/1259367515.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.h

  2%|██▎                                                                                               | 285/12356 [00:00<00:08, 1423.26it/s]/tmp/ipykernel_18850/1259367515.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["ATG"][row] = freqs["ATG"]
/tmp/ipykernel_18850/1259367515.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["GTG"][row] = freqs["GTG"]
/tmp/ipykernel_18850/1259367515.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.h

  3%|███▍                                                                                              | 428/12356 [00:00<00:08, 1330.77it/s]/tmp/ipykernel_18850/1259367515.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["ATG"][row] = freqs["ATG"]
/tmp/ipykernel_18850/1259367515.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["GTG"][row] = 0
/tmp/ipykernel_18850/1259367515.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returni

  5%|████▍                                                                                             | 564/12356 [00:00<00:08, 1341.30it/s]/tmp/ipykernel_18850/1259367515.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["ATG"][row] = freqs["ATG"]
/tmp/ipykernel_18850/1259367515.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["GTG"][row] = 0
/tmp/ipykernel_18850/1259367515.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returni

...

 97%|█████████████████████████████████████████████████████████████████████████████████████████████▏  | 11986/12356 [00:08<00:00, 1408.26it/s]/tmp/ipykernel_18850/1259367515.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["ATG"][row] = freqs["ATG"]
/tmp/ipykernel_18850/1259367515.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["GTG"][row] = 0
/tmp/ipykernel_18850/1259367515.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returni

 98%|██████████████████████████████████████████████████████████████████████████████████████████████▎ | 12135/12356 [00:08<00:00, 1429.82it/s]/tmp/ipykernel_18850/1259367515.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["ATG"][row] = freqs["ATG"]
/tmp/ipykernel_18850/1259367515.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["GTG"][row] = 0
/tmp/ipykernel_18850/1259367515.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returni

/tmp/ipykernel_18850/1259367515.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["ATG"][row] = freqs["ATG"]
/tmp/ipykernel_18850/1259367515.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["GTG"][row] = 0
/tmp/ipykernel_18850/1259367515.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["TTG"][row] = 0
/tmp/ipykernel_18850/1259367515.py:23: SettingWithCopyWarning: 
A value is trying to b

 99%|███████████████████████████████████████████████████████████████████████████████████████████████▍| 12279/12356 [00:08<00:00, 1428.63it/s]/tmp/ipykernel_18850/1259367515.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["ATG"][row] = freqs["ATG"]
/tmp/ipykernel_18850/1259367515.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  start_codons["GTG"][row] = 0
/tmp/ipykernel_18850/1259367515.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returni

100%|████████████████████████████████████████████████████████████████████████████████████████████████| 12356/12356 [00:08<00:00, 1428.75it/s]


In [8]:
# Computing uniformity of start-codon per ortologus row
start_codons["uniformity"] = "NA"
for row in range(len(start_codons)):
    if len(set(start_codons.iloc[row, 1])) == 1:
        start_codons.iloc[row, 5] = "same"
    else:
        start_codons.iloc[row, 5] = "different"

In [9]:
# Constructing table withh all data about the ortologus rows (including pararows)
start_codons2 = start_codons.merge(orto_rows, on="ortologus_row", how="outer")

In [10]:
# Creating a table, combining data about gene and its start-codone
strain_gene_row = start_codons2[["Species", "Genes", "ortologus_row", "uniformity", "ATG", "GTG", "TTG"]]   # Other codons deleted
summary_rows = df1.merge(strain_gene_row, on="ortologus_row")

In [37]:
# Assigning cog to orto_row
row_cog = row_assigner.merge(df1[["id", "cog"]], on="id").groupby("ortologus_row").agg({"cog": "max"})
start_codons2 = start_codons2.merge(row_cog, on="ortologus_row")

ortologus_row                                       start_codons   ATG  \
0                 69  [ATG, ATG, ATG, ATG, ATG, ATG, ATG, ATG, ATG, ...  19.0   
1                 70  [ATG, ATG, ATG, ATG, ATG, ATG, ATG, ATG, ATG, ...  19.0   
2                 71  [GTG, GTG, GTG, GTG, GTG, GTG, GTG, GTG, GTG, ...   0.0   
3                 72  [ATG, ATG, ATG, ATG, ATG, ATG, ATG, ATG, ATG, ...  19.0   
4                 73  [ATG, ATG, ATG, ATG, ATG, ATG, ATG, ATG, ATG, ...  19.0   
...              ...                                                ...   ...   
12351          13157                                              [TTG]   0.0   
12352          13158                                              [ATG]   1.0   
12353          13159                                              [TTG]   0.0   
12354          13160                                              [ATG]   1.0   
12355          13161                                              [TTG]   0.0   

        GTG  TTG uniformity  Species  Genes         Alg.-Conn.  \
0       0.0  0.0       same       19     19  @1000977878:0.845   
1       0.0  0.0       same       19     19   @100160862:0.846   
2      19.0  0.0       same       19     19  @1001753132:0.852   
3       0.0  0.0       same       19     19  @1003063236:0.855   
4       0.0  0.0       same       19     19  @1004275350:0.844   
...     ...  ...        ...      ...    ...                ...   
12351   0.0  1.0       same        1      1                  0   
12352   0.0  0.0       same        1      1                  0   
12353   0.0  1.0       same        1      1                  0   
12354   0.0  0.0       same        1      1                  0   
12355   0.0  1.0       same        1      1                  0   

                  V_campbellii0.fasta  ...             V_campbellii18.fasta  \
0      BCFIDHHG_01172_V_campbellii0_3  ...  NCEBMCKE_02821_V_campbellii18_3   
1      BCFIDHHG_02799_V_campbellii0_3  ...  NCEBMCKE_00977_V_campbellii18_3   
2      BCFIDHHG_01530_V_campbellii0_3  ...  NCEBMCKE_02403_V_campbellii18_3   
3      BCFIDHHG_02245_V_campbellii0_3  ...  NCEBMCKE_01652_V_campbellii18_3   
4      BCFIDHHG_02807_V_campbellii0_3  ...  NCEBMCKE_00967_V_campbellii18_3   
...                               ...  ...                              ...   
12351                               *  ...                                *   
12352                               *  ...                                *   
12353                               *  ...                                *   
12354                               *  ...                                *   
12355                               *  ...                                *   

                  V_campbellii2.fasta             V_campbellii3.fasta  \
0      JKJHJJCD_01087_V_campbellii2_3  EIKCGOEP_02111_V_campbellii3_6   
1      JKJHJJCD_02830_V_campbellii2_3  EIKCGOEP_00545_V_campbellii3_6   
2      JKJHJJCD_01536_V_campbellii2_3  EIKCGOEP_01790_V_campbellii3_6   
3      JKJHJJCD_02250_V_campbellii2_3  EIKCGOEP_01100_V_campbellii3_6   
4      JKJHJJCD_02838_V_campbellii2_3  EIKCGOEP_00536_V_campbellii3_6   
...                               ...                             ...   
12351                               *                               *   
12352                               *                               *   
12353                               *                               *   
12354                               *                               *   
12355                               *                               *   

                  V_campbellii4.fasta             V_campbellii5.fasta  \
0      LDIFMMON_03055_V_campbellii4_3  NHMGMJLF_00422_V_campbellii5_5   
1      LDIFMMON_01530_V_campbellii4_3  NHMGMJLF_02078_V_campbellii5_5   
2      LDIFMMON_02739_V_campbellii4_3  NHMGMJLF_00785_V_campbellii5_5   
3      LDIFMMON_02095_V_campbellii4_3  NHMGMJLF_01476_V_campbellii5_5   
4      LDIFMMON_01522_V_campbellii4_3  NHMGMJLF_02

In [47]:
# Adding organism_name to datasets
summary_rows["organism"] = folder_name
start_codons2["organism"] = folder_name

ortologus_row                                       start_codons   ATG  \
0                 69  [ATG, ATG, ATG, ATG, ATG, ATG, ATG, ATG, ATG, ...  19.0   
1                 70  [ATG, ATG, ATG, ATG, ATG, ATG, ATG, ATG, ATG, ...  19.0   
2                 71  [GTG, GTG, GTG, GTG, GTG, GTG, GTG, GTG, GTG, ...   0.0   
3                 72  [ATG, ATG, ATG, ATG, ATG, ATG, ATG, ATG, ATG, ...  19.0   
4                 73  [ATG, ATG, ATG, ATG, ATG, ATG, ATG, ATG, ATG, ...  19.0   
...              ...                                                ...   ...   
13156           8816                                                NaN   NaN   
13157           8817                                                NaN   NaN   
13158           8818                                                NaN   NaN   
13159           8819                                                NaN   NaN   
13160           8820                                                NaN   NaN   

        GTG  TTG uniformity  Species  Genes         Alg.-Conn.  \
0       0.0  0.0       same       19     19  @1000977878:0.845   
1       0.0  0.0       same       19     19   @100160862:0.846   
2      19.0  0.0       same       19     19  @1001753132:0.852   
3       0.0  0.0       same       19     19  @1003063236:0.855   
4       0.0  0.0       same       19     19  @1004275350:0.844   
...     ...  ...        ...      ...    ...                ...   
13156   NaN  NaN        NaN        1      2       @903321600:1   
13157   NaN  NaN        NaN        1      2       @932121448:1   
13158   NaN  NaN        NaN        1      2          @948600:1   
13159   NaN  NaN        NaN        1      2       @949581092:1   
13160   NaN  NaN        NaN        1      2       @973012000:1   

                  V_campbellii0.fasta  ...             V_campbellii18.fasta  \
0      BCFIDHHG_01172_V_campbellii0_3  ...  NCEBMCKE_02821_V_campbellii18_3   
1      BCFIDHHG_02799_V_campbellii0_3  ...  NCEBMCKE_00977_V_campbellii18_3   
2      BCFIDHHG_01530_V_campbellii0_3  ...  NCEBMCKE_02403_V_campbellii18_3   
3      BCFIDHHG_02245_V_campbellii0_3  ...  NCEBMCKE_01652_V_campbellii18_3   
4      BCFIDHHG_02807_V_campbellii0_3  ...  NCEBMCKE_00967_V_campbellii18_3   
...                               ...  ...                              ...   
13156                               *  ...                                *   
13157                               *  ...                                *   
13158                               *  ...                                *   
13159                               *  ...                                *   
13160                               *  ...                                *   

                  V_campbellii2.fasta  \
0      JKJHJJCD_01087_V_campbellii2_3   
1      JKJHJJCD_02830_V_campbellii2_3   
2      JKJHJJCD_01536_V_campbellii2_3   
3      JKJHJJCD_02250_V_campbellii2_3   
4      JKJHJJCD_02838_V_campbellii2_3   
...                               ...   
13156                               *   
13157                               *   
13158                               *   
13159                               *   
13160                               *   

                                     V_campbellii3.fasta  \
0                         EIKCGOEP_02111_V_campbellii3_6   
1                         EIKCGOEP_00545_V_campbellii3_6   
2                         EIKCGOEP_01790_V_campbellii3_6   
3                         EIKCGOEP_01100_V_campbellii3_6   
4                         EIKCGOEP_00536_V_campbellii3_6   
...                                                  ...   
13156  PDCNNCFJ_00089_V_campbellii3_3,PDCNNCFJ_00020_...   
13157  ADOFKCCL_01854_V_campbellii3_5,ADOFKCCL_01859_...   
13158                                                  *   
13159  PDCNNCFJ_00058_V_campbellii3_3,DJBJBNNG_00025_...   
13160                                                  *   

                  V_campbellii4.fasta  \
0      LDIFMMON_03055_V_campbellii4_3

We need to align only rows with different start-codons.

In [14]:
# non_uniform_or_list = list(set(start_codons2.query("uniformity == 'different'").ortologus_row))
# for orto_row in tqdm(non_uniform_or_list):
#     subset = summary_rows.query("ortologus_row == @orto_row")
#     with open (f"../{folder_name}/data/multialignments/{folder_name}_withoutp_{str(orto_row)}.fasta", "w") as nucleotide_fasta:
#         for index, row in subset.iterrows():
#             #if row['type_of_the_gene'] != "pseudogene": # It will be actual when we found pseudogenes again
#             nucleotide_fasta.write(">")
#             nucleotide_fasta.write(row["id"])
#             nucleotide_fasta.write("_")
#             nucleotide_fasta.write(row["source"])
#             nucleotide_fasta.write("_")
#             nucleotide_fasta.write(row["start_codone"])
#             nucleotide_fasta.write("\n")
#             nucleotide_fasta.write(row["n_sequence"])
#             nucleotide_fasta.write("\n")

#### Saving summary-rows and start-codons2

In [15]:
#summary_rows.to_csv(f"../{folder_name}/data/summary_rows_prokka.csv", index=False)

In [16]:
#start_codons2.to_csv(f"../{folder_name}/data/start_codons2_prokka.csv", index=False)